random forest for refined dataset
- imputed with mean value of each column
- eliminate outliers and leverges after normalized

some observations:
- the model contructed by not normalized dataset is as good as the normalized dataset.

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
from sklearn.ensemble import RandomForestRegressor

from sklearn.preprocessing import normalize
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

from sklearn.model_selection import RandomizedSearchCV, GridSearchCV, cross_val_score
from sklearn.metrics import mean_squared_error, r2_score

from sklearn import tree
import joblib

import scipy

In [3]:
plt.rcParams["figure.figsize"] = (15, 10)

## load data

In [4]:
pth_data = '../processed_data/train_refine_not_norm_min.csv'
df_refine = pd.read_csv(pth_data)

In [5]:
df_refine

height  weight  gender        bmi   age      rh  heart_rate  \
0      1.63    50.0     1.0  18.818924  23.0  39.890   70.500000   
1      1.74    65.0    -1.0  21.469150  23.0  51.680   76.298872   
2      1.77    68.0    -1.0  21.705129  24.0  55.748   66.000000   
3      1.63    50.0     1.0  18.818924  23.0  34.850   74.000000   
4      1.77    58.0    -1.0  18.513199  23.0  51.275   97.000000   
..      ...     ...     ...        ...   ...     ...         ...   
280    1.63    50.0     1.0  18.818924  23.0  55.330   65.000000   
281    1.69    75.0    -1.0  26.259585  24.0  31.690   70.000000   
282    1.69    75.0    -1.0  26.259585  24.0  25.660  105.000000   
283    1.71    64.0    -1.0  21.887076  27.0  42.280   59.000000   
284    1.71    64.0    -1.0  21.887076  27.0  56.110   70.000000   

     stress_level  skin_temp       eda   Clo  Act   env_temp  
0       10.000000  32.215000  0.146231  0.50  1.0  24.931111  
1       23.987342  31.672874  0.877379  0.36  1.0  26.781111  
2        6.000000  33.353000  0.033414  0.54  1.0  23.592778  
3       20.000000  31.672874  0.068829  0.50  1.0  23.868889  
4       76.500000  32.215000  0.006481  0.36  1.0  25.427778  
..            ...        ...       ...   ...  ...        ...  
280      9.000000  31.672874  0.009863  0.50  0.8  24.835000  
281      0.000000  32.007000  0.012317  0.36  1.0  23.772778  
282     23.987342  30.484000  0.002907  0.36  1.8  23.966111  
283     23.000000  33.996000  0.068711  0.74  1.0  24.157778  
284     24.000000  34.073000  0.107164  0.74  1.0  20.805000  

[285 rows x 13 columns]

In [6]:
df_refine.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 285 entries, 0 to 284
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   height        285 non-null    float64
 1   weight        285 non-null    float64
 2   gender        285 non-null    float64
 3   bmi           285 non-null    float64
 4   age           285 non-null    float64
 5   rh            285 non-null    float64
 6   heart_rate    285 non-null    float64
 7   stress_level  285 non-null    float64
 8   skin_temp     285 non-null    float64
 9   eda           285 non-null    float64
 10  Clo           285 non-null    float64
 11  Act           285 non-null    float64
 12  env_temp      285 non-null    float64
dtypes: float64(13)
memory usage: 29.1 KB


## data process

### X & y

In [7]:
X_data = df_refine[['height', 'weight', 'gender', 'bmi', 'age', 'rh', \
                      'heart_rate', 'stress_level', 'skin_temp', 'eda', \
                      'Clo', 'Act']]

In [8]:
X_cols_name = X_data.columns

In [9]:
y_data = df_refine['env_temp']

### make training data and testing data

In [10]:
X_train, X_test, y_train, y_test = train_test_split(X_data, y_data, test_size=0.2, random_state=1208)

much better than the basic linear regression

## 5-fold cross validation
tuning hyperparameter

### random search
Use the random grid to search for best hyperparameters (approximately)
- 5-fold cross validation

In [11]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# Number of features to consider at every split
max_features = ['auto', 'sqrt']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 20]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 8, 16]

# Complexity parameter used for Minimal Cost-Complexity Pruning.
# ccp_alpha = [0.00001, 0.0005, 0.0001, 0.0005]
    
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [12]:
random_grid

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'min_samples_split': [2, 5, 10, 15, 20],
 'min_samples_leaf': [1, 2, 4, 8, 16]}

In [13]:
rfr = RandomForestRegressor()

In [14]:
rfr_random = RandomizedSearchCV(estimator=rfr, 
                               param_distributions=random_grid, 
                               n_iter=100, 
                               cv=5, 
                               verbose=2, 
                               random_state=1208, 
                               n_jobs=-1,
                               scoring='r2')

In [15]:
# Fit the random search model
# Use R^2 as score method
rfr_random.fit(X_train, y_train)

Fitting 5 folds for each of 100 candidates, totalling 500 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    7.6s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   40.1s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.6min
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  2.3min finished


RandomizedSearchCV(cv=5, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4, 8, 16],
                                        'min_samples_split': [2, 5, 10, 15, 20],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=1208, scoring='r2', verbose=2)

In [16]:
rfr_random.best_params_

{'n_estimators': 1000,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'sqrt',
 'max_depth': 90}

In [17]:
rfr_random.best_score_

0.4575072484208433

### Grid Search
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try.

In [18]:
bp = rfr_random.best_params_
ne = bp['n_estimators']
md = bp['max_depth']
md = md if md is not None else 5
param_grid = {
    'n_estimators': [int(ne * 0.8), int(ne * 0.9), ne, int(ne * 1.1), int(ne * 1.2)],
    'min_samples_split': [1, 2, 3],
    'min_samples_leaf': [1, 2, 3],
    'max_features': [2, 3, 4, 5],
    'max_depth': [int(md * 0.8), int(md * 0.9), md, int(md * 1.1), int(md * 1.2), None]
}

In [19]:
rfr = RandomForestRegressor()

In [20]:
grid_search = GridSearchCV(estimator = rfr, 
                           param_grid = param_grid, 
                           cv = 5, 
                           n_jobs = -1, 
                           verbose = 2,
                           scoring='r2')

In [21]:
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 1080 candidates, totalling 5400 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    7.3s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   34.0s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.3min
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  2.4min
[Parallel(n_jobs=-1)]: Done 989 tasks      | elapsed:  3.8min
[Parallel(n_jobs=-1)]: Done 1434 tasks      | elapsed:  5.6min
[Parallel(n_jobs=-1)]: Done 1961 tasks      | elapsed:  7.6min
[Parallel(n_jobs=-1)]: Done 2568 tasks      | elapsed:  9.9min
[Parallel(n_jobs=-1)]: Done 3257 tasks      | elapsed: 12.6min
[Parallel(n_jobs=-1)]: Done 4026 tasks      | elapsed: 15.5min
[Parallel(n_jobs=-1)]: Done 4877 tasks      | elapsed: 18.8min
[Parallel(n_jobs=-1)]: Done 5400 out of 5400 | elapsed: 20.9min finished


GridSearchCV(cv=5, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'max_depth': [72, 81, 90, 99, 108, None],
                         'max_features': [2, 3, 4, 5],
                         'min_samples_leaf': [1, 2, 3],
                         'min_samples_split': [1, 2, 3],
                         'n_estimators': [800, 900, 1000, 1100, 1200]},
             scoring='r2', verbose=2)

In [22]:
grid_search.best_params_

{'max_depth': None,
 'max_features': 3,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 1000}

In [23]:
grid_search.best_score_

0.46294489317116827

### validate the result

In [24]:
best_params_5 = grid_search.best_params_

In [25]:
rfr = RandomForestRegressor(random_state=1208)

In [26]:
rfr.set_params(**best_params_5)

RandomForestRegressor(max_features=3, n_estimators=1000, random_state=1208)

In [27]:
rfr_cv_mse = cross_val_score(rfr, X_train, y_train, scoring='neg_mean_squared_error', cv=5)

In [28]:
rfr_cv_mse

array([-0.70538098, -0.95033088, -0.59938594, -0.70921344, -0.44534684])

In [29]:
np.abs(rfr_cv_mse.mean())

0.68193161571975

In [30]:
rfr_cv_r2 = cross_val_score(rfr, X_train, y_train, scoring='r2', cv=5)

In [31]:
rfr_cv_r2

array([0.37486474, 0.24751231, 0.6145736 , 0.50027198, 0.52164097])

In [32]:
rfr_cv_r2.mean()

0.45177271955891934

In [33]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params_5)

RandomForestRegressor(max_features=3, n_estimators=1000, random_state=1208)

In [34]:
rfr_best.fit(X_train, y_train)

RandomForestRegressor(max_features=3, n_estimators=1000, random_state=1208)

### save model

In [35]:
filename = './min_random_forest_model_5.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model_5.sav']

## 7-fold cross validation
tuning hyperparameter

### random search
Use the random grid to search for best hyperparameters (approximately)
- 10-fold cross validation

In [36]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# Number of features to consider at every split
max_features = ['auto', 'sqrt']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 20]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 8, 16]

# Complexity parameter used for Minimal Cost-Complexity Pruning.
# ccp_alpha = [0.00001, 0.0005, 0.0001, 0.0005]
    
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [37]:
random_grid

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'min_samples_split': [2, 5, 10, 15, 20],
 'min_samples_leaf': [1, 2, 4, 8, 16]}

In [38]:
rfr = RandomForestRegressor()

In [39]:
rfr_random = RandomizedSearchCV(estimator=rfr, 
                               param_distributions=random_grid, 
                               n_iter=100, 
                               cv=7, 
                               verbose=2, 
                               random_state=1208, 
                               n_jobs=-1,
                               scoring='r2')

In [40]:
# Fit the random search model
# Use R^2 as score method
rfr_random.fit(X_train, y_train)

Fitting 7 folds for each of 100 candidates, totalling 700 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    4.9s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   37.4s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.4min
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  2.8min
[Parallel(n_jobs=-1)]: Done 700 out of 700 | elapsed:  3.1min finished


RandomizedSearchCV(cv=7, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4, 8, 16],
                                        'min_samples_split': [2, 5, 10, 15, 20],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=1208, scoring='r2', verbose=2)

In [41]:
rfr_random.best_params_

{'n_estimators': 600,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'auto',
 'max_depth': 20}

In [42]:
rfr_random.best_score_

0.47078616486206776

### Grid Search
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try.

In [43]:
bp = rfr_random.best_params_
ne = bp['n_estimators']
md = bp['max_depth']
md = md if md is not None else 5
param_grid = {
    'n_estimators': [int(ne * 0.8), int(ne * 0.9), ne, int(ne * 1.1), int(ne * 1.2)],
    'min_samples_split': [1, 2, 3],
    'min_samples_leaf': [1, 2, 3],
    'max_features': [2, 3, 4, 5],
    'max_depth': [int(md * 0.8), int(md * 0.9), md, int(md * 1.1), int(md * 1.2), None]
}

In [44]:
rfr = RandomForestRegressor()

In [45]:
grid_search = GridSearchCV(estimator = rfr, 
                           param_grid = param_grid, 
                           cv = 7, 
                           n_jobs = -1, 
                           verbose = 2,
                           scoring='r2')

In [46]:
grid_search.fit(X_train, y_train)

Fitting 7 folds for each of 1080 candidates, totalling 7560 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    4.2s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   23.7s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:   54.9s
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  1.5min
[Parallel(n_jobs=-1)]: Done 989 tasks      | elapsed:  2.7min
[Parallel(n_jobs=-1)]: Done 1434 tasks      | elapsed:  4.5min
[Parallel(n_jobs=-1)]: Done 1961 tasks      | elapsed:  6.2min
[Parallel(n_jobs=-1)]: Done 2568 tasks      | elapsed:  8.0min
[Parallel(n_jobs=-1)]: Done 3257 tasks      | elapsed:  9.9min
[Parallel(n_jobs=-1)]: Done 4026 tasks      | elapsed: 12.3min
[Parallel(n_jobs=-1)]: Done 4877 tasks      | elapsed: 14.7min
[Parallel(n_jobs=-1)]: Done 5808 tasks      | elapsed: 17.5min
[Parallel(n_jobs=-1)]: Done 6821 tasks      | elapsed: 20.4min
[Parallel(n_jobs=-1)]: Done 7560 out of 7560 | elapsed: 22.6min finished


GridSearchCV(cv=7, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'max_depth': [16, 18, 20, 22, 24, None],
                         'max_features': [2, 3, 4, 5],
                         'min_samples_leaf': [1, 2, 3],
                         'min_samples_split': [1, 2, 3],
                         'n_estimators': [480, 540, 600, 660, 720]},
             scoring='r2', verbose=2)

In [47]:
grid_search.best_params_

{'max_depth': 20,
 'max_features': 5,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 720}

In [48]:
grid_search.best_score_

0.4768876128771474

### validate the result

In [49]:
best_params_7 = grid_search.best_params_

In [50]:
rfr = RandomForestRegressor(random_state=1208)

In [51]:
rfr.set_params(**best_params_7)

RandomForestRegressor(max_depth=20, max_features=5, n_estimators=720,
                      random_state=1208)

In [52]:
rfr_cv_mse = cross_val_score(rfr, X_train, y_train, scoring='neg_mean_squared_error', cv=5)

In [53]:
rfr_cv_mse

array([-0.71562029, -0.97866759, -0.56226536, -0.70505189, -0.43811714])

In [54]:
np.abs(rfr_cv_mse.mean())

0.6799444525547567

In [55]:
rfr_cv_r2 = cross_val_score(rfr, X_train, y_train, scoring='r2', cv=5)

In [56]:
rfr_cv_r2

array([0.36579027, 0.22507484, 0.63844345, 0.5032043 , 0.52940658])

In [57]:
rfr_cv_r2.mean()

0.45238389009245045

In [58]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params_7)

RandomForestRegressor(max_depth=20, max_features=5, n_estimators=720,
                      random_state=1208)

In [59]:
rfr_best.fit(X_train, y_train)

RandomForestRegressor(max_depth=20, max_features=5, n_estimators=720,
                      random_state=1208)

### save model

In [60]:
filename = './min_random_forest_model_7.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model_7.sav']

## 10-fold cross validation
tuning hyperparameter

### random search
Use the random grid to search for best hyperparameters (approximately)
- 10-fold cross validation

In [61]:
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]

# Number of features to consider at every split
max_features = ['auto', 'sqrt']

# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)

# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 20]

# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 8, 16]

# Complexity parameter used for Minimal Cost-Complexity Pruning.
# ccp_alpha = [0.00001, 0.0005, 0.0001, 0.0005]
    
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [62]:
random_grid

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None],
 'min_samples_split': [2, 5, 10, 15, 20],
 'min_samples_leaf': [1, 2, 4, 8, 16]}

In [63]:
rfr = RandomForestRegressor()

In [64]:
rfr_random = RandomizedSearchCV(estimator=rfr, 
                               param_distributions=random_grid, 
                               n_iter=100, 
                               cv=10, 
                               verbose=2, 
                               random_state=1208, 
                               n_jobs=-1,
                               scoring='r2')

In [65]:
# Fit the random search model
# Use R^2 as score method
rfr_random.fit(X_train, y_train)

Fitting 10 folds for each of 100 candidates, totalling 1000 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    6.5s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   38.6s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.5min
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  2.8min
[Parallel(n_jobs=-1)]: Done 1000 out of 1000 | elapsed:  4.7min finished


RandomizedSearchCV(cv=10, estimator=RandomForestRegressor(), n_iter=100,
                   n_jobs=-1,
                   param_distributions={'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, 80, 90, 100, 110,
                                                      None],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 4, 8, 16],
                                        'min_samples_split': [2, 5, 10, 15, 20],
                                        'n_estimators': [200, 400, 600, 800,
                                                         1000, 1200, 1400, 1600,
                                                         1800, 2000]},
                   random_state=1208, scoring='r2', verbose=2)

In [66]:
rfr_random.best_params_

{'n_estimators': 600,
 'min_samples_split': 2,
 'min_samples_leaf': 1,
 'max_features': 'auto',
 'max_depth': 20}

In [67]:
rfr_random.best_score_

0.4720244602913959

### Grid Search
Random search allowed us to narrow down the range for each hyperparameter. Now that we know where to concentrate our search, we can explicitly specify every combination of settings to try.

In [68]:
bp = rfr_random.best_params_
ne = bp['n_estimators']
md = bp['max_depth']
md = md if md is not None else 5
param_grid = {
    'n_estimators': [int(ne * 0.8), int(ne * 0.9), ne, int(ne * 1.1), int(ne * 1.2)],
    'min_samples_split': [1, 2, 3],
    'min_samples_leaf': [1, 2, 3],
    'max_features': [2, 3, 4, 5],
    'max_depth': [int(md * 0.8), int(md * 0.9), md, int(md * 1.1), int(md * 1.2), None]
}

In [69]:
rfr = RandomForestRegressor()

In [70]:
grid_search = GridSearchCV(estimator = rfr, 
                           param_grid = param_grid, 
                           cv = 10, 
                           n_jobs = -1, 
                           verbose = 2,
                           scoring='r2')

In [71]:
grid_search.fit(X_train, y_train)

Fitting 10 folds for each of 1080 candidates, totalling 10800 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done  17 tasks      | elapsed:    4.9s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:   26.2s
[Parallel(n_jobs=-1)]: Done 341 tasks      | elapsed:  1.0min
[Parallel(n_jobs=-1)]: Done 624 tasks      | elapsed:  1.8min
[Parallel(n_jobs=-1)]: Done 989 tasks      | elapsed:  2.9min
[Parallel(n_jobs=-1)]: Done 1434 tasks      | elapsed:  4.1min
[Parallel(n_jobs=-1)]: Done 1961 tasks      | elapsed:  5.6min
[Parallel(n_jobs=-1)]: Done 2568 tasks      | elapsed:  7.2min
[Parallel(n_jobs=-1)]: Done 3257 tasks      | elapsed:  9.2min
[Parallel(n_jobs=-1)]: Done 4026 tasks      | elapsed: 11.4min
[Parallel(n_jobs=-1)]: Done 4877 tasks      | elapsed: 13.8min
[Parallel(n_jobs=-1)]: Done 5808 tasks      | elapsed: 16.4min
[Parallel(n_jobs=-1)]: Done 6821 tasks      | elapsed: 19.3min
[Parallel(n_jobs=-1)]: Done 7914 tasks      | elapsed: 22.3min
[Parallel(n_jobs=-1)]: Done 9089 tasks      | 

GridSearchCV(cv=10, estimator=RandomForestRegressor(), n_jobs=-1,
             param_grid={'max_depth': [16, 18, 20, 22, 24, None],
                         'max_features': [2, 3, 4, 5],
                         'min_samples_leaf': [1, 2, 3],
                         'min_samples_split': [1, 2, 3],
                         'n_estimators': [480, 540, 600, 660, 720]},
             scoring='r2', verbose=2)

In [72]:
grid_search.best_params_

{'max_depth': 20,
 'max_features': 3,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'n_estimators': 480}

In [73]:
grid_search.best_score_

0.48021719999278856

### validate the result

In [74]:
best_params_10 = grid_search.best_params_

In [75]:
rfr = RandomForestRegressor(random_state=1208)

In [76]:
rfr.set_params(**best_params_10)

RandomForestRegressor(max_depth=20, max_features=3, n_estimators=480,
                      random_state=1208)

In [77]:
rfr_cv_mse = cross_val_score(rfr, X_train, y_train, scoring='neg_mean_squared_error', cv=5)

In [78]:
rfr_cv_mse

array([-0.69364694, -0.9419856 , -0.58594564, -0.73845767, -0.44103768])

In [79]:
np.abs(rfr_cv_mse.mean())

0.6802147074273682

In [80]:
rfr_cv_r2 = cross_val_score(rfr, X_train, y_train, scoring='r2', cv=5)

In [81]:
rfr_cv_r2

array([0.38526389, 0.25412024, 0.62321618, 0.47966583, 0.52626955])

In [82]:
rfr_cv_r2.mean()

0.4537071384257974

In [83]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params_10)

RandomForestRegressor(max_depth=20, max_features=3, n_estimators=480,
                      random_state=1208)

In [84]:
rfr_best.fit(X_train, y_train)

RandomForestRegressor(max_depth=20, max_features=3, n_estimators=480,
                      random_state=1208)

### save model

In [85]:
filename = './min_random_forest_model_10.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model_10.sav']

## final model

In [86]:
best_params = grid_search.best_params_

In [87]:
rfr_best = RandomForestRegressor(random_state=1208)
rfr_best.set_params(**best_params)

RandomForestRegressor(max_depth=20, max_features=3, n_estimators=480,
                      random_state=1208)

In [88]:
rfr_best.fit(X_train, y_train)

RandomForestRegressor(max_depth=20, max_features=3, n_estimators=480,
                      random_state=1208)

### save model

In [89]:
filename = './min_random_forest_model.sav'
joblib.dump(rfr_best, filename)

['./min_random_forest_model.sav']

## visualization
pick a tree from the forest to visualize

In [90]:
plt.rcParams["figure.figsize"] = (600, 100)
a_tree = tree.plot_tree(rfr_best.estimators_[0], 
                        feature_names=X_data.columns, 
                        rounded=True,
                        filled=True,
                        fontsize=12)

## test

In [91]:
y_pred_test = rfr_best.predict(X_test)

In [92]:
y_pred_test

array([25.44036941, 25.46763214, 24.41454745, 24.30847003, 25.18832407,
       24.26348032, 25.06051215, 23.8025706 , 24.46558912, 25.0050625 ,
       24.68368403, 24.74662153, 24.02696296, 24.32523958, 24.83440509,
       24.6941794 , 23.912     , 24.0347446 , 24.37434028, 24.02503472,
       23.5637662 , 25.16809259, 23.908625  , 23.66677431, 25.2109294 ,
       24.02904061, 24.01406366, 24.87760185, 22.98154398, 25.06806481,
       24.36365972, 25.33479398, 24.61299421, 24.09762616, 24.90424306,
       23.83358449, 24.81524672, 24.02012731, 24.12263079, 24.67009568,
       23.13755093, 24.13900231, 24.3212662 , 24.26652431, 22.67534954,
       24.53751244, 24.12100231, 24.27957639, 24.68502662, 25.36268461,
       23.6534537 , 24.85530208, 24.72193576, 23.67936343, 24.01928067,
       24.12596209, 24.79369552])

In [93]:
pd.DataFrame({'Actual': y_test, 'Predicted': y_pred_test})

Actual  Predicted
166  25.841111  25.440369
25   26.390000  25.467632
229  24.641111  24.414547
217  23.868889  24.308470
10   24.737778  25.188324
71   23.677222  24.263480
100  24.545000  25.060512
152  23.003889  23.802571
145  24.652778  24.465589
238  25.282778  25.005062
235  25.016111  24.683684
53   25.318889  24.746622
232  23.772778  24.026963
157  24.545000  24.325240
282  23.966111  24.834405
28   24.750000  24.694179
123  23.712778  23.912000
23   23.677222  24.034745
24   24.545000  24.374340
48   24.062222  24.025035
68   21.867222  23.563766
165  25.027778  25.168093
7    23.868889  23.908625
19   23.483889  23.666774
255  25.671111  25.210929
54   24.062222  24.029041
124  23.868889  24.014064
101  25.307222  24.877602
11   22.632778  22.981544
200  25.318889  25.068065
256  23.677222  24.363660
203  25.597778  25.334794
183  24.581111  24.612994
155  23.483889  24.097626
276  24.835000  24.904243
49   23.808889  23.833584
189  25.210000  24.815247
212  24.157778  24.020127
83   23.196111  24.122631
136  24.171111  24.670096
107  23.545000  23.137551
161  23.772778  24.139002
259  24.545000  24.321266
180  25.162222  24.266524
37   21.915000  22.675350
27   24.255000  24.537512
204  24.255000  24.121002
234  25.016111  24.279576
134  24.122222  24.685027
52   26.097222  25.362685
252  24.545000  23.653454
267  25.318889  24.855302
177  23.905000  24.721936
216  23.665000  23.679363
117  24.157778  24.019281
246  23.292222  24.125962
4    25.427778  24.793696

In [94]:
# mean squared error
mean_squared_error(y_test, y_pred_test)

0.2822273010375085

In [95]:
# R2 score
r2_score(y_test, y_pred_test)

0.6663878688396566

## save test dataset

In [96]:
test_df = X_test.copy()

In [97]:
test_df['env_temp'] = 0

In [98]:
test_df['env_temp'] = y_test

In [99]:
test_df.to_csv('../processed_data/test_min.csv')

In [100]:
test_df

height  weight  gender        bmi   age      rh  heart_rate  \
166    1.77    68.0    -1.0  21.705129  24.0  57.779   76.298872   
25     1.83    74.0    -1.0  22.096808  24.0  46.650   84.000000   
229    1.63    50.0     1.0  18.818924  23.0  41.050   86.000000   
217    1.63    50.0     1.0  18.818924  23.0  39.170   67.000000   
10     1.63    50.0     1.0  18.818924  23.0  54.550   79.000000   
71     1.69    75.0    -1.0  26.259585  24.0  28.920  102.000000   
100    1.63    50.0     1.0  18.818924  23.0  51.410   76.298872   
152    1.67    56.0     1.0  20.079601  26.0  59.560   76.298872   
145    1.77    68.0    -1.0  21.705129  24.0  53.962   86.000000   
238    1.77    58.0    -1.0  18.513199  23.0  53.134   92.000000   
235    1.77    68.0    -1.0  21.705129  24.0  60.468   84.000000   
53     1.63    50.0     1.0  18.818924  23.0  52.990   70.000000   
232    1.78    73.0    -1.0  23.040020  24.0  65.000   87.000000   
157    1.63    50.0     1.0  18.818924  23.0  40.740   76.000000   
282    1.69    75.0    -1.0  26.259585  24.0  25.660  105.000000   
28     1.77    68.0    -1.0  21.705129  24.0  55.759   78.000000   
123    1.77    68.0    -1.0  21.705129  24.0  54.895   63.500000   
23     1.63    50.0     1.0  18.818924  23.0  31.880   61.500000   
24     1.69    75.0    -1.0  26.259585  24.0  28.900   86.000000   
48     1.69    75.0    -1.0  26.259585  24.0  33.440   76.298872   
68     1.60    52.5     1.0  20.507812  24.0  48.105   77.000000   
165    1.69    75.0    -1.0  26.259585  24.0  50.720  106.000000   
7      1.63    50.0     1.0  18.818924  23.0  28.430   67.000000   
19     1.63    50.0     1.0  18.818924  23.0  21.910   65.000000   
255    1.77    58.0    -1.0  18.513199  23.0  54.292   88.000000   
54     1.63    50.0     1.0  18.818924  23.0  34.870   72.000000   
124    1.69    75.0    -1.0  26.259585  24.0  33.130   76.298872   
101    1.77    58.0    -1.0  18.513199  23.0  52.915   80.000000   
11     1.60    52.5     1.0  20.507812  24.0  34.698   85.000000   
200    1.63    50.0     1.0  18.818924  23.0  53.260   84.000000   
256    1.69    75.0    -1.0  26.259585  24.0  26.190   92.000000   
203    1.64    54.0     1.0  20.077335  24.0  61.437   73.000000   
183    1.77    68.0    -1.0  21.705129  24.0  50.876   77.000000   
155    1.63    50.0     1.0  18.818924  23.0  30.710   78.000000   
276    1.63    50.0     1.0  18.818924  23.0  54.670   64.000000   
49     1.60    52.5     1.0  20.507812  24.0  42.886   61.000000   
189    1.77    68.0    -1.0  21.705129  24.0  56.012   76.298872   
212    1.63    50.0     1.0  18.818924  23.0  25.740   76.000000   
83     1.63    50.0     1.0  18.818924  23.0  30.790   65.500000   
136    1.77    68.0    -1.0  21.705129  24.0  50.374   76.000000   
107    1.60    52.5     1.0  20.507812  24.0  40.279   69.500000   
161    1.63    50.0     1.0  18.818924  23.0  26.550   60.000000   
259    1.71    64.0    -1.0  21.887076  27.0  57.270   76.298872   
180    1.60    52.5     1.0  20.507812  24.0  50.664   76.298872   
37     1.60    52.5     1.0  20.507812  24.0  44.556   72.000000   
27     1.63    50.0     1.0  18.818924  23.0  39.370   76.000000   
204    1.69    75.0    -1.0  26.259585  24.0  34.490   69.000000   
234    1.77    68.0    -1.0  21.705129  24.0  55.204   69.000000   
134    1.77    68.0    -1.0  21.705129  24.0  50.400   85.000000   
52     1.69    75.0    -1.0  26.259585  24.0  54.760   90.000000   
252    1.71    64.0    -1.0  21.887076  27.0  41.380   62.000000   
267    1.63    50.0     1.0  18.818924  23.0  54.400   71.500000   
177    1.77    68.0    -1.0  21.705129  24.0  55.296   94.000000   
216    1.77    68.0    -1.0  21.705129  24.0  56.068   61.000000   
117    1.66    57.0     1.0  20.685150  25.0  41.950   76.298872   
246    1.63    50.0     1.0  18.818924  23.0  30.370   79.000000   
4      1.77    58.0    -1.0  18.513199  23.0  51.275   97.000000   

     stress_level  skin_temp       eda   Clo  Act   env_temp